In [9]:
import geopandas as gpd
import folium

In [10]:
wse_gdf = gpd.read_file(r'Z:\js\ResMap\py\output\2yr Existing\tempfiles\ras_wse.shp')
wse_gdf.to_crs(epsg=4326, inplace=True)
# Compute depth as [max_wse - min_elev]
wse_gdf['depth_max'] = wse_gdf['wse_max'] - wse_gdf['min_elev']
wse_gdf['depth_max'] = wse_gdf['depth_max'].round(2)
wse_gdf.crs

<Geographic 2D CRS: EPSG:4326>
Name: WGS 84
Axis Info [ellipsoidal]:
- Lat[north]: Geodetic latitude (degree)
- Lon[east]: Geodetic longitude (degree)
Area of Use:
- name: World.
- bounds: (-180.0, -90.0, 180.0, 90.0)
Datum: World Geodetic System 1984 ensemble
- Ellipsoid: WGS 84
- Prime Meridian: Greenwich

In [11]:
max_wse_gdf = wse_gdf[['geometry', 'min_elev', 'wse_max', 'depth_max']]
max_wse_gdf.shape

(10436, 4)

In [12]:
max_wse_gdf = max_wse_gdf[max_wse_gdf['depth_max'] > 0]
max_wse_gdf.shape

(535, 4)

In [20]:
f = folium.Figure(width=800, height=550)
m = folium.Map(location=[30.87, -93.29],tiles='cartodbpositron', zoom_start=13, min_zoom = 10, max_zoom=15).add_to(f)

In [21]:
wse_style = lambda x: {
    "color": "#E5214E",
    "fill": False,
    "opacity": 1
}
clip_style = lambda x: {
    "color": "#21E5D6",
    "fill": False,
    "opacity": 1
}

In [23]:
g = folium.GeoJson(data=max_wse_gdf, style_function=wse_style).add_to(m)
# folium.GeoJsonTooltip(
#     fields=["depth_max", "wse_max", "min_elev"],
#     aliases=["Depth:", "WSE:", "Elevation:"]
# ).add_to(g)

m

In [16]:
# Clip to Ras Mapper extracted Depth Extent
bounds_gdf = gpd.read_file(r'Z:\js\ResMap\data\westPark\2yr Existing Depth.geojson')
bounds_gdf.crs

<Geographic 2D CRS: EPSG:4326>
Name: WGS 84
Axis Info [ellipsoidal]:
- Lat[north]: Geodetic latitude (degree)
- Lon[east]: Geodetic longitude (degree)
Area of Use:
- name: World.
- bounds: (-180.0, -90.0, 180.0, 90.0)
Datum: World Geodetic System 1984 ensemble
- Ellipsoid: WGS 84
- Prime Meridian: Greenwich

In [17]:
tooltip_clip_gdf = gpd.clip(max_wse_gdf, bounds_gdf) 

In [24]:
g = folium.GeoJson(data=tooltip_clip_gdf, style_function=clip_style).add_to(m)
folium.GeoJsonTooltip(
    fields=["depth_max", "wse_max", "min_elev"],
    aliases=["Depth:", "WSE:", "Elevation:"]
).add_to(g)

m